# Packages

In [23]:
#path: /Users/winde/Library/Python/3.8/lib/python/site-packages
!pip3 install Bio
!pip3 install pandas
!pip3 install requests
!pip3 install ete3

Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip available: 22.3.1 -> 23.0
[notice] To update, run: /Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip
Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip available: 22.3.1 -> 23.0
[notice] To update, run: /Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip
Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip available: 22.3.1 -> 23.0
[notice] To update, run: /Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip
Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip available: 22.3.1 -> 23.0
[notice] To update, run: /Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip


In [24]:
import sys
sys.path.append("/Users/winde/Library/Python/3.8/lib/python/site-packages")

# Generic functions

In [25]:
def sizefastafile (inputfile):
    """Count the number of protein sequences in a given fasta file"""
    with open (inputfile) as file:
        size = 0
        for line in file:
            if line.startswith(">"):
                size += 1
                
    return size

# Extract CAZy family sequences

In [26]:
#give the the family you want to retrieve the GenBank ID's from
#family can be GH, GT, PL, CE, AA or CBM followed by a number (without a space)

family = 'GH116'

#Following files will be saved locally:

# 1) the raw text file from CAZy
# 2) a txt file with the GenBank ID's
# 3) a fasta file with the FASTA sequences

In [27]:
#import the necessary modules

import pandas as pd
import requests
import Bio
from Bio import Entrez
from Bio import SeqIO
from urllib.request import HTTPError
from tqdm import tqdm

Entrez.email = 'alex.windels@ugent.be'

#pandas configuration
pd.set_option('display.max_rows', None)

In [28]:
#script

def CAZy_extract(family, data):
    """This function extracts the GenBank IDs from a CAZy family and builds a FASTA file with corresponding protein
    sequences"""
    
    print(f'Writing the {family} CAZy data file')
    with open('CAZy_data_'+family+'.txt','w') as file:
        file.write(data)

    df = pd.read_table('CAZy_data_'+family+'.txt',engine = 'python', header=None)
    df = df.iloc[:, -1]
    output = df.to_string(index=False)
    print(f'Writing the {family} GenBank ID file')
    with open('CAZy_' + family + '_GenBankIDs.txt', 'w') as file:
        file.write(output)
    with open('CAZy_' + family + '_GenBankIDs.txt', 'r') as file:
        total_length = len(file.readlines()) #can't be integrated in the next lines: tqdm(file, total) because files gets closed

    print(f'Extracting protein sequences from NCBI')
    fastasequences = ''
    with open('CAZy_' + family + '_GenBankIDs.txt', 'r') as file:
        for line in tqdm(file, total = total_length):
            try:
                handle = Entrez.efetch("Protein", id = line, retmode = "text", rettype = "fasta")
                try:
                    seq_record = SeqIO.read(handle, "fasta")
                except:
                    print("Something went wrong, let's skip this one.")
                    break  # Something went wrong retrieving data
                thisoutput = ">"+seq_record.description+"\n"+str(seq_record.seq)+"\n"
                fastasequences = fastasequences + thisoutput
                handle.close()
            except HTTPError:
                print("HTTP Error. Let's try waiting for a little bit.")
            # time.sleep(1)

    return fastasequences

#create an outputfile


print(f'Working on family {family}')
#url
url = 'http://www.cazy.org/IMG/cazy_data/'+family+'.txt'
print(f'Retrieving data from page {url}')
response = requests.get(url)
data = response.text
#extract GenBank ID's from this page
result = CAZy_extract(family,data)

print(f'Writing {family} FASTA sequences file')
with open('CAZy_'+family+'_FASTA_sequences.fasta','w') as file:
    print(result)
    file.write(result)

print('Finished!')

Working on family GH116
Retrieving data from page http://www.cazy.org/IMG/cazy_data/GH116.txt
Writing the GH116 CAZy data file
Writing the GH116 GenBank ID file
Extracting protein sequences from NCBI


100%|███████████████████████████████████████| 1117/1117 [16:28<00:00,  1.13it/s]

Writing GH116 FASTA sequences file
>BCM90545.1 hypothetical protein IAD21_02399 [Abditibacteriota bacterium]
MKALILSMAMVAVTMAFRAPVGADSFEPGTGTIVDARWKSGLPLGGVGVGKIELLTDGSFGNLTNQHNWDRPYGWAKGAFAAIQVQGANGTSTARLLRLGSANEYTGVENIAHTRMQGWFPRAEIAFADAALPVQVKLDAFSPLVPHNPKDSSLPVARFDYTLTNPSRQRVKASVLLAWPNLLGWGGKTNVKWDDVSGASQSAANAGGLHGLRYATTQSYTDQRQNVLGEDFLGARQELGITITTCPSWDAAATTPSFWKNFAATGQLHPAADGAPAQSAGAVAATVDLAPGQSRTVHFTLAWAMPHMVTVQQREQSDLVLQSQVPPTAPIAQRWTTSHFMVPGDTVTVDLGRATKPDSLTFDQGGTPEDYPRGLRVEVSSDGKNWQQVAQKTEDGIRTSIQNGKFTVALSPVAGRFVRLTNLGSSVDKWWSIHALQAHDADGNQTLSFVPVGTPQAVEDTGHYWQNFWKGAPEIASYADQNSERLLRETRAWQDPVRASSLPFWLKLKLVNCTFPLFSNTVLTRNGRFAVLESPIDMGGALGTMDQRMASHAFYTAFFPELDRAELEMFADCQQKDGRITHFDGNVHEVVGRPDVGYGITDWPDLSCSWVMQAAKLYRWTGDEAYLQRIQPHIGRAMTWLDSNAQTDGFIPAGGSTYDYEQLPRGAFIYSASCYLGALRSAAAVGTPDQAKVYDARLLQTQNAVMSQLWNGTYFRKWKQLETDKTVDDSFVANMAGDWLARLSGMPRTLAPNIIHQSIAQTIARHQKPFFPVPPMQVTSEGRATTSSCYFLQHEPFLGCEAIYENYVDDGLETLRRVYLSSWELNHSPWDQSLAYDAPAGPQGGLVTYMTCPTSWFVLNALGGTSLDVPHRVLYVSPRLATSERELHIPV

# Exclude sequences not available in UniParc


In [31]:
#import necessary modules
import hashlib
import sys
import xml.etree.ElementTree as ET
from urllib.parse import urlencode
from urllib.request import urlopen

#inputfile
inputfile = 'CAZy_'+family+'_FASTA_sequences.fasta'

#outputfile
outputfile = 'CAZy_'+family+'_Verfied_FASTA_sequences.fasta'

#API url
URL = "https://www.ebi.ac.uk/interpro/match-lookup/matches"

In [32]:
#Here we generate a file only containing UNIQUE sequences that can be used for InterPro domain detection
def parse_fasta(inputfile):
    """This function parses trough a given FASTA file and creates a dict of ID: sequence"""
    proteins = {}
    
    with open(inputfile, 'r') as file:
        for seq_record in SeqIO.parse(file, "fasta"):
            proteins[seq_record.id] = str(seq_record.seq)
    
    #print(proteins.items())
    return proteins

def check_uniparc(proteins):
    """This function checks wich sequences have a UniParc ID and thus can be used for InterPro domain detection"""
    
    md5_to_id = {}
    
    #converts the protein sequences to a hexadecimal representation in uppercase
    for identifier, sequence in proteins.items():
        md5 = hashlib.md5(sequence.encode()).hexdigest().upper()
        md5_to_id[md5] = identifier
    
        
    #print(md5_to_id)
    params = {"md5": list(md5_to_id.keys())}
    #print(params)
    data = urlencode(params, doseq=True).encode("ascii")
    #print(data)
    
    with urlopen(URL, data) as res:
        data = res.read().decode("utf-8")
    
    domain_ids = []
    unknown_ids = []
    root = ET.fromstring(data)
    for m in root.findall(".//match"):
        md5 = m.find("proteinMD5").text
        protein_id = md5_to_id.pop(md5) #are these the ID's of proteins that have a UniParc Identifier?
        domain_ids.append(protein_id)
        #print(protein_id)

        #find domains on InterPro
        for hit in m.findall("hit"):
            #print(hit)
            columns = hit.text.split(",")
            
            fragments = []
            for frag in columns[6].split(";"):
                start, end, _ = frag.split("-")
                fragments.append((int(start), int(end)))

    for protein_id in md5_to_id.values():
        unknown_ids.append(protein_id)
        
    
    #print(domain_ids)
    
    #print(len(domain_ids))
    #print(unknown_ids)
    #print(len(unknown_ids))
    
    print(f'{len(domain_ids)} out of {len(domain_ids) + len(unknown_ids)} unique sequences will be included')
    print(f'{len(unknown_ids)} sequences cant be found in UniParc and will be excluded: {unknown_ids} \n' )
    return domain_ids

def verified_sequences(domain_ids, inputfile):
    output = ''

    with open(inputfile, 'r') as file:
        for seq_record in SeqIO.parse(file, "fasta"):

            if str(seq_record.id) in domain_ids:
                output += '>' + str(seq_record.description) + '\n' + str(seq_record.seq) + '\n'
         
    with open (outputfile, 'w') as f:
        f.write(output)

    print(output)
    return output

#verseq = verified_sequences(check_uniparc(parse_fasta(inputfile)), inputfile)
uniparccheck = check_uniparc(parse_fasta(inputfile))
verseq = verified_sequences(uniparccheck, inputfile)

print(uniparccheck)

853 out of 898 unique sequences will be included
45 sequences cant be found in UniParc and will be excluded: ['UJR25817.1', 'UJR11626.1', 'UJR15607.1', 'QNF75010.1', 'QHN86501.1', 'QHO32478.1', 'QHN98001.1', 'QHO32654.1', 'QHO35236.1', 'QHO32486.1', 'QHO32475.1', 'QHO13614.1', 'UVP53705.1', 'UVP51679.1', 'QUT66521.1', 'CAH8536627.1', 'UFP97055.1', 'CAH8588056.1', 'CAH2076649.1', 'BDF45835.1', 'WAL58203.1', 'UZQ54603.1', 'QNF30091.1', 'UOY04960.1', 'UOY04935.1', 'WAR00764.1', 'CAD5921506.1', 'BDB99689.1', 'BDB99447.1', 'CAH8578054.1', 'CAH8580573.1', 'CAH8590213.1', 'CAH8597707.1', 'CAH8579848.1', 'CAH8556092.1', 'CAH8596573.1', 'CAI2730606.1', 'CAH8520588.1', 'UFH56585.1', 'CAH8854862.1', 'WBR99928.1', 'UZO80290.1', 'WBB61597.1', 'WBB59050.1', 'BDO40596.1'] 

>BCM90545.1 hypothetical protein IAD21_02399 [Abditibacteriota bacterium]
MKALILSMAMVAVTMAFRAPVGADSFEPGTGTIVDARWKSGLPLGGVGVGKIELLTDGSFGNLTNQHNWDRPYGWAKGAFAAIQVQGANGTSTARLLRLGSANEYTGVENIAHTRMQGWFPRAEIAFADAALPVQVKLDAFSPLVPHNPKDSSLPV

# Format FASTA file

In [33]:
# DESCRIPTION A fasta file will be formatted to remove duplicate sequences, and to remove duplicate identifiers.

# EXAMPLES
# >gi|2660639|emb|CAA04523.1| alpha-glucan phosphorylase [Thermotoga maritima]
# will be changed to
# >2660639
# 
# >gi|754097242|ref|WP_041736169.1| alpha-glucan phosphorylase [Coprothermobacter proteolyticus] >gi|639380266|gb|ACI17870.2| alpha-glucan phosphorylase [Coprothermobacter proteolyticus DSM 5265]
# will be changed to
# >754097242
# 
# And if multiple identifiers contain the exact same sequence, only one is retained.

# Route to the fasta files
fastafile = 'CAZy_'+family+'_Verfied_FASTA_sequences.fasta'
outputfile_name = 'CAZy_'+family+'_FASTA_sequences_formatted.fasta'

In [34]:
sequence_list = []
id_list = []

output = ''

with open(fastafile,'r') as file:
    for seq_record in SeqIO.parse(file, "fasta"):
        if seq_record.seq not in sequence_list:
            sequence_list.append(seq_record.seq)
            if seq_record.id not in id_list:
                id_list.append(seq_record.id)
                    
                desc = seq_record.description
                tax = desc[desc.find('[') + 1:desc.find(']')]
                tax = tax.replace(' ', '_')
                output += '>' + seq_record.id + '_' + tax + '\n' + seq_record.seq + '\n'
            else:
                print('ID in id_list')
                break
    
with open(outputfile_name, 'w') as f:
    f.write(str(output))
    
print(output)


>BCM90545.1_Abditibacteriota_bacterium
MKALILSMAMVAVTMAFRAPVGADSFEPGTGTIVDARWKSGLPLGGVGVGKIELLTDGSFGNLTNQHNWDRPYGWAKGAFAAIQVQGANGTSTARLLRLGSANEYTGVENIAHTRMQGWFPRAEIAFADAALPVQVKLDAFSPLVPHNPKDSSLPVARFDYTLTNPSRQRVKASVLLAWPNLLGWGGKTNVKWDDVSGASQSAANAGGLHGLRYATTQSYTDQRQNVLGEDFLGARQELGITITTCPSWDAAATTPSFWKNFAATGQLHPAADGAPAQSAGAVAATVDLAPGQSRTVHFTLAWAMPHMVTVQQREQSDLVLQSQVPPTAPIAQRWTTSHFMVPGDTVTVDLGRATKPDSLTFDQGGTPEDYPRGLRVEVSSDGKNWQQVAQKTEDGIRTSIQNGKFTVALSPVAGRFVRLTNLGSSVDKWWSIHALQAHDADGNQTLSFVPVGTPQAVEDTGHYWQNFWKGAPEIASYADQNSERLLRETRAWQDPVRASSLPFWLKLKLVNCTFPLFSNTVLTRNGRFAVLESPIDMGGALGTMDQRMASHAFYTAFFPELDRAELEMFADCQQKDGRITHFDGNVHEVVGRPDVGYGITDWPDLSCSWVMQAAKLYRWTGDEAYLQRIQPHIGRAMTWLDSNAQTDGFIPAGGSTYDYEQLPRGAFIYSASCYLGALRSAAAVGTPDQAKVYDARLLQTQNAVMSQLWNGTYFRKWKQLETDKTVDDSFVANMAGDWLARLSGMPRTLAPNIIHQSIAQTIARHQKPFFPVPPMQVTSEGRATTSSCYFLQHEPFLGCEAIYENYVDDGLETLRRVYLSSWELNHSPWDQSLAYDAPAGPQGGLVTYMTCPTSWFVLNALGGTSLDVPHRVLYVSPRLATSERELHIPVFFPRFWGTLDYIPATRRLTLRVDRVFEVDGKIQSSLYHTVGASGDAVSGVSIAAIAADGDAPLIRLPRPF

# Clustering sequences: CD-HIT

In [35]:
#cluster cut-off

clustercutoff = 0.85

#name of the input file

inputfastafile = 'CAZy_'+family+'_FASTA_sequences_formatted.fasta'

#name of the output file

outputfastafile = 'CAZy_'+family+'_FASTA_sequences_formatted_'+"{0:.0%}".format(clustercutoff)+'.fasta'

#path of cd-hit exe

cdhit = r"/Users/winde/Alex/Doctoraat/PyEED/Jupyter Notebooks/cd-hit"

In [36]:
#run CD-HIT

from subprocess import Popen, PIPE

cdhit_process = Popen([cdhit, "-i", inputfastafile, "-o", outputfastafile, "-c", str(clustercutoff)], stdout=PIPE, stderr=PIPE)
stdout, stderr = cdhit_process.communicate()

print(f"Number of sequences of the inputfile: {sizefastafile(inputfastafile)} ")
print(f"Number of sequences of the outputfile after clustering at {clustercutoff}: {sizefastafile(outputfastafile)}")
print('Finished!')

Number of sequences of the inputfile: 853 
Number of sequences of the outputfile after clustering at 0.85: 473
Finished!


# Include characterized sequences

In [37]:
# This script checks if characterized enzymes are retained in the file after clustering and adds the full description of the characterized enzymes

#name of the inputfile
inputfile = 'CAZy_'+family+'_FASTA_sequences_formatted_'+"{0:.0%}".format(clustercutoff)+'.fasta'
outputfile = 'CAZy_'+family+'_formatted_'+"{0:.0%}".format(clustercutoff)+'inclchar.fasta'

#Following files will be saved locally:
# 1. A TXT file with the characterized GenBANK ID's from the CAZy family
# 2. A FASTA file with the characterized FASTA sequences corresponding to the ID's
# 3. A FASTA file containing the clustered sequences WITH all characterized sequences

In [38]:
#import the necessary modules
import pandas as pd
from tabulate import tabulate
import requests
import Bio
from Bio import Entrez
from Bio import SeqIO
from urllib.request import HTTPError
from tqdm import tqdm

#pandas configuration
pd.set_option("display.max_rows", None, "display.max_columns", None, 'display.max_colwidth', None)

Entrez.email = 'alex.windels@ugent.be'

In [39]:
#script

#number of pages with characterized enzymes
df = pd.read_html('http://www.cazy.org/'+family+'_characterized.html#pagination_FUNC')[1][4]
if str(df.iloc[0]) != 'nan':
    pages = df.iloc[0].count('|') - 1
    
else:
    pages = 1
    

def extract_characterized(url):
    """Extract GenBank ID's of characterized proteins from CAZy"""
    df = pd.read_html(url)[1][4]
    df = df.drop_duplicates()
    output = df.to_list()
    id_list = ''
    for element in output:
        element = str(element)
        pointposition = element.find('.')
        if pointposition != -1:
            element = element[:pointposition + 2]
            if element not in id_list:
                id_list += element + '\n'

    return id_list

def CAZy_extract(data):
    """Convert extracted GenBank ID's to FASTA sequences"""
    
    total_length = data.count('\n')

    print(f'Extracting FASTA sequences from NCBI')
    fastasequences = ''
    with open(f'Characterized_{family}_GenBankID_file.txt', 'r') as file:
        for line in tqdm(file, total = total_length):
            try:
                handle = Entrez.efetch("Protein", id = line, retmode = "text", rettype = "fasta")
                try:
                    seq_record = SeqIO.read(handle, "fasta")
                except:
                    print("Something went wrong, let's skip this one.")
                    break  # Something went wrong retrieving data
            
                thisoutput = ">"+seq_record.id[0:str(seq_record).find('.')+1] + " "+ seq_record.description[str(seq_record.description).find('[')+1:str(seq_record.description).find(']')]+"\n"+str(seq_record.seq)+"\n"
                thisoutput = thisoutput.replace(' ','_')
                fastasequences = fastasequences + thisoutput
                handle.close()
            except HTTPError:
                print("HTTP Error. Let's try waiting for a little bit.")
            # time.sleep(1)

    return fastasequences

characterized_ID = ''
for page in range(pages):
    url = 'http://www.cazy.org/'+family+'_characterized.html?debut_FUNC='+str(page)+'00#pagination_FUNC'
    print(f'Retrieving data from page {url}')
    characterized_ID += extract_characterized(url)

print(f'Writing {family} Characterized GenBank ID file')
with open(f'Characterized_{family}_GenBankID_file.txt', 'w') as file:
    file.write(characterized_ID)

characterized_sequences = CAZy_extract(characterized_ID)
print(f'Writing {family} Characterized FASTA sequences file')
with open(f'Characterized_{family}_FASTA_sequences.fasta', 'w') as file:
    file.write(characterized_sequences)


Retrieving data from page http://www.cazy.org/GH116_characterized.html?debut_FUNC=000#pagination_FUNC
Writing GH116 Characterized GenBank ID file
Extracting FASTA sequences from NCBI


100%|█████████████████████████████████████████████| 5/5 [00:06<00:00,  1.20s/it]

Writing GH116 Characterized FASTA sequences file


In [40]:
#verify that the GenBank IDs of the characterized sequences are included in the uniparccheck list 

check = 1
verified_IDs = []
no_uniparc = []
with open(f'Characterized_{family}_GenBankID_file.txt','r') as file:
    file = file.readlines()
    for ID in file:
        ID = ID.strip()
        if ID in uniparccheck:
            print(f'{ID}: UniParc ID found')
            verified_IDs.append(ID)
            check += 1
        else:
            no_uniparc.append(ID)
            print(f'Warning: No UniParc entry not found for {ID}. A BLAST step will be performed.')
            check += 1
    
    if check == len(file):
        print('Finished!')

print(no_uniparc)

AEF18218.1: UniParc ID found
NP_065995.1: UniParc ID found
CAM17042.1: UniParc ID found
['AAK41589.1', 'AAK43141.1']


In [42]:
from Bio.Blast import NCBIWWW
from Bio.Blast import NCBIXML

infile = f'Characterized_{family}_FASTA_sequences.fasta'

def blast_char_id(infile, no_uniparc, verified_IDs):
    #default identity threshold is 90%. Anything lower may result in different domain compositions.
    identity_threshold = 90
    E_value_tresh = 1e-20 

    #output a dictionary with characterized GenBank ID's that we found an appropriate Uniprot ID for using BLASTP
    outputblastdict = {}
    outputchar = []
    charblastdict = {}

    with open (infile, 'r') as file:
        #go over each protein sequence in the characterized fasta file
        for seq_record in SeqIO.parse(file, "fasta"):
            ID = seq_record.id
            ID = ID[:ID.find('_')]

            #if the ID is also present in the list of characterized ID's without corresponding Uniprot ID, blast the sequence
            if ID in no_uniparc:
                charidlist = []
                identitydict = {}
                print(seq_record.id)
                print('Doing a BLASTP search')
                result_handle = NCBIWWW.qblast("blastp", "nr", seq_record.seq)
                print('Going over BLAST results')

                #go over the blast results
                blast_records = NCBIXML.parse(result_handle)
                for blast_record in blast_records:
                    for alignment in blast_record.alignments:
                        #print(alignment)
                        for hsp in alignment.hsps:
                            proteinsequence = hsp.sbjct
                            #print(proteinsequence)
                            identity = hsp.identities / hsp.align_length * 100
                            if identity >= identity_threshold:
                                #add this id to list
                                charidlist.append(alignment.accession)
                                #add this id with corresponding identity to dict
                                identitydict[alignment.accession] = float("{:.2f}".format(identity))
                                outputblastdict[alignment.accession] = proteinsequence

                #use the InterPro API to check for UniParc matches. check_uniparc takes a dict as input
                if len(outputblastdict) != 0:
                    inuniparc = check_uniparc(outputblastdict)
        
                #create a new dictionary with matches:identity for matches that have a UniParc ID
                newiddict = {}
        
                #if there is a UniParc identifier for the found BLAST matches:
                if len(inuniparc) != 0:
                    for ele in inuniparc:
                        if ele in identitydict:
                            newiddict[ele] = identitydict[ele]

                    #use the match with highest identity to the query
                    maxid = max(newiddict, key = newiddict.get)

                    #add the ID to the verified_IDs list
                    verified_IDs.append(ID)
                    charblastdict[ID] = maxid
                    print(f'For characterized sequence {ID}, {maxid} ({newiddict[maxid]}% identical) will be used for domain-detection')

                else:
                    print(f'Sorry no good match could be found for {ID} ')


    
    print(charblastdict)
    print('Finished!')
    return charblastdict, outputblastdict
 
blastchar = blast_char_id(infile, no_uniparc, verified_IDs)

AAK41589.1_Saccharolobus_solfataricus_P2
Doing a BLASTP search
Going over BLAST results
1 out of 2 unique sequences will be included
1 sequences cant be found in UniParc and will be excluded: ['SAI85024'] 

For characterized sequence AAK41589.1, WP_010923346 (100.0% identical) will be used for domain-detection
AAK43141.1_Saccharolobus_solfataricus_P2
Doing a BLASTP search
Going over BLAST results
5 out of 7 unique sequences will be included
2 sequences cant be found in UniParc and will be excluded: ['SAI85024', 'WP_252973155'] 

For characterized sequence AAK43141.1, WP_010924105 (100.0% identical) will be used for domain-detection
{'AAK41589.1': 'WP_010923346', 'AAK43141.1': 'WP_010924105'}
Finished!


In [45]:

#following code checks if the ID's of characterized enzymes are present in the FASTA sequences file. If so it removes the ID and sequence
#afterwards all ID's and sequences of characterized enzymes are added at the end of the file
print('Creating a file containing clustered sequences and all characterized sequences with corresponding CAZy description')

with open(outputfile,'w') as f:
    for seq in SeqIO.parse(inputfile,'fasta'):
        if seq.id.find('_') >2: 
            proteinidentifier = seq.id.split('_')[0]
        else:
            proteinidentifier = seq.id.split('_')[0]+'_'+seq.id.split('_')[1]
        
        if proteinidentifier not in verified_IDs:
            SeqIO.write(seq,f,"fasta")
   
    charoutput = ''
    with open (f'Characterized_{family}_FASTA_sequences.fasta','r') as r:
        for seq_record in SeqIO.parse(r, 'fasta'):
            if seq_record.id.find('_') >2: 
                proteinidentifier = seq_record.id.split('_')[0]
                
            else:
                proteinidentifier = seq_record.id.split('_')[0]+'_'+seq_record.id.split('_')[1]
            
            print(proteinidentifier)
            if proteinidentifier in verified_IDs:# or seq_record.id.split('_')[0] in outputchar:
                
                #for the characterised ID's we did a succesful BLAST search for:
                if proteinidentifier in blastchar[0]:
                    charoutput += '>' + seq_record.id + '\n' + blastchar[1][blastchar[0][proteinidentifier]]+ '\n'
                    
                #for all other characterised ID's
                else:
                    charoutput += '>' + seq_record.id + '\n' + seq_record.seq + '\n'
                

    print('Writing '+ outputfile + '\n' )
    f.write(str(charoutput))
    
    print(charoutput)
with open(outputfile,'r') as f:
    print(f.read())

    
#print(output)

print(f"Number of sequences of the outputfile after including characterized sequences: {sizefastafile(outputfile)}") 
print('Finished!')

Creating a file containing clustered sequences and all characterized sequences with corresponding CAZy description
AAK41589.1
AAK43141.1
AEF18218.1
NP_065995.1
CAM17042.1
Writing CAZy_GH116_formatted_85%inclchar.fasta

>AAK41589.1_Saccharolobus_solfataricus_P2
MVTYTDKDRIVAGVPLGGIGTGKLEIDNKVRITNITIRNNWGNPIKLLRGFHIYIKPKDKRGFLFQKDSGLYKVSEFRGEILYEGKYPVVTVKGKNDDVEVVLEAFSSIIPRDVKNSSLPAVGISLRVKGSREGIVAISFPNIVGSVSIGRLNERIRNGVIHKNIKANDYDPAKGNTSLISENVSKIITQYNLKRKPSETINFWLSQYENEEPWVKLDREEEVTDDPHEVTGHRDDPASILISNYSEGDEIRYVFAWYFTGKHVFYPYGHYYENFFKDSLEVAKYFLDNFNELRNKIFHNIVNVKDWLGDAIINSAYILSSNTWLDEKGRFAIYEAPQNCPYLGTIGACYEFGSLPVILMFPELEKSFLKLLIRHIREDGYVPHDLGYHSLDSPIDGTTSPPRWKDMNPSLILLVYRYFKFTNDIEFLKEVYPILVKVMDWELRQCKGNLPFMEGEMDNAFDATIIKGHDSYTSSLFIGSLIAMREIAKLVGDSNYVDFISEKLSSAREAFRRMFNGRYFKAWDSVDNASFLAQLYGEWFTTLVGLEDIVEEDIIKKALESIIRLNGNASPHCVPNLVDDNGKIVGLSVQTYSSWPRMVFAICWLAYKKGVGDLSFCKKEWDNLVKNGMVWDQPSRINGYNGKAEMNYLDHYIGSPSPWSFLF
>AAK43141.1_Saccharolobus_solfataricus_P2
MKYKYSYVLDSGVPLGGIGTGSMEIRADGRLYS

# MSA: ClustalO

In [46]:
from Bio.Align.Applications import ClustalOmegaCommandline
from Bio import SeqIO
from Bio import AlignIO
import os

In [47]:
#path of clustalo_exe

clustalo_exe = r"/Users/winde/Alex/Doctoraat/PyEED/Jupyter Notebooks/clustalo"

In [48]:
#name of the input file
in_file = 'CAZy_'+family+'_formatted_'+"{0:.0%}".format(clustercutoff)+'inclchar.fasta'

#name you want to give to the outputfile
out_file = 'CAZy_'+family+'_formatted_'+"{0:.0%}".format(clustercutoff)+'_aligned.fasta'


In [49]:
#perform the multiple sequence alignment using ClustalOmega

clustalOmega_cline = ClustalOmegaCommandline( clustalo_exe, infile=in_file,outfile = out_file)

assert os.path.isfile(clustalo_exe), "Clustalo executable missing"
stdout, stderr = clustalOmega_cline()

#visualize the alignment
alignment = AlignIO.read(out_file, 'fasta')
for record in alignment:
    print(record.format("fasta"))

>BCM90545.1_Abditibacteriota_bacterium
------------------------------------------------------------
------------------------------------------------------------
------------------------------------------------------------
------------------------------------------------------------
------------------------------------------------------------
------------------------------------------------------------
------------------------------------------------------------
------------------------------------------------------------
------------------------------------------------------------
------------------------------------------------------------
------------------------------------------------------------
------------------------------------------------------------
------------------------------------------------------------
------------------------------------------------------------
------------------------------------------------------------
MKAL-I-------------------------------------LSM

# Phylogenetic tree: FastTree

In [50]:
from Bio import Phylo
from Bio.Phylo.PhyloXML import Phylogeny
from io import StringIO
import matplotlib
import matplotlib.pyplot as plt

In [51]:
#name of the inputfile

inputfile = 'CAZy_'+family+'_formatted_'+"{0:.0%}".format(clustercutoff)+'_aligned.fasta'

#name of the outputfile

outputfile = 'CAZy_'+family+'phyltree.nwk'

#path to FastTree

FastTree = '/Users/winde/Alex/Doctoraat/PyEED/Jupyter Notebooks/FastTree'

In [52]:
from subprocess import Popen, PIPE

fasttree_process = Popen([FastTree, "-nt", "-gtr", "-quiet", "-out", outputfile, inputfile], stdout=PIPE, stderr=PIPE)
stdout, stderr = fasttree_process.communicate()

#create a phyloxml file as well
phyloxmloutput = 'CAzy_'+family+'phyltree.xml'
Phylo.convert(outputfile, "newick", phyloxmloutput, "phyloxml")

print(f'{outputfile} and {phyloxmloutput} finished!')


CAZy_GH116phyltree.nwk and CAzy_GH116phyltree.xml finished!


In [53]:
#import the necessary modules
from ete3 import Tree, TreeStyle, TextFace, NodeStyle

In [54]:
with open(f'Characterized_{family}_GenBankID_file.txt', 'r') as file:
    listwithcharacterisedIDs = []
    file = file.read().strip().split('\n')
    for line in file:
        listwithcharacterisedIDs.append(line)
print(listwithcharacterisedIDs)

['AAK41589.1', 'AAK43141.1', 'AEF18218.1', 'NP_065995.1', 'CAM17042.1']


In [55]:

#load the tree
t = Tree(outputfile)

#use Treestyle to make some modifications
ts = TreeStyle()


#show the leaf labels on the tee leafs
ts.show_leaf_name = True

#circular representation 
ts.mode = "c"
ts.arc_start = -180 # 0 degrees = 3 o'clock
ts.arc_span = 359

ts.scale = None
ts.optimal_scale_level = 'mid'

#add title
ts.title.add_face(TextFace(f"{family} Phylogenetic Tree", fsize=40), column=0)

#color the labels of characterized sequences
for node in t.traverse():
    if node.is_leaf():
        
        for ID in listwithcharacterisedIDs:
            if ID in node.name:

                #make a label that has the name of the leaf and color it blue
                name_face = TextFace(node.name, fgcolor="#0112EB", fsize=10)               
                node.add_face(name_face, column=0, position='branch-right')
                
                #delete the original leaf name or it will overlap with the label
                node.name = ''

    
#output the tree

#t.show(tree_style=ts)



# Domain detection: InterPro

In [56]:
#import necessary modules

from urllib import request
from urllib.error import HTTPError
from time import sleep
import json
import sys, errno, re, json, ssl


In [57]:
#create a list of IDs that need to be fetched using the InterPro API
interprolist = []

#go in the order of leaves in the phylogenetic tree

tree = Phylo.read(outputfile, 'newick')
for leaf in tree.find_clades(terminal=True):
    leaf = str(leaf)
    genbankid = leaf[:leaf.find('_')]
    interprolist.append(genbankid)
        
    
print(interprolist)
print(len(interprolist))

['AFY45032.1', 'QLE41800.1', 'BAZ68399.1', 'QLE57510.1', 'BAZ06285.1', 'NP', 'AGY57706.1', 'CAN94573.1', 'ACO61507.1', 'EEH53657.1', 'ABX02953.1', 'AEF18218.1', 'AEU36563.1', 'ADV81312.1', 'QNI34795.1', 'ABF40689.1', 'AQQ71109.1', 'AYY13601.1', 'UPK77053.1', 'BAB13431.1', 'NP', 'BAD32491.1', 'CAM17042.1', 'CAI10981.1', 'EDL02462.1', 'AAI60640.1', 'balche', 'VUY95630.1', 'CAG12815.1', 'balche', 'AWO97544.1', 'AHH37418.1', 'AFO96150.1', 'XP', 'CAB3248405.1', 'CAH0702348.1', 'CAH0714467.1', 'CAH2991170.1', 'CAG9785611.1', 'CAH0581399.1', 'CAF3001293.1', 'CAG9821274.1', 'CAH1113965.1', 'CAG9854271.1', 'CAG9829466.1', 'QQP35851.1', 'CAG9765704.1', 'CAH0551459.1', 'CAH0392186.1', 'CAM17043.1', 'CCD79502.1', 'CAH8576533.1', 'CAH8559416.1', 'CAH8854016.1', 'VUY95629.1', 'CAD7281356.1', 'CAG9812317.1', 'CAD7223927.1', 'ALC39944.1', 'AHN54442.1', 'NP', 'EAT47379.1', 'CAD7086392.1', 'ULU14455.1', 'NP', 'ADC68237.1', 'CEF63815.1', 'ADY40283.1', 'ULT87090.1', 'NP', 'UJR23091.1', 'CAD7195306.1', 'AD

In [58]:
#import packages
from operator import itemgetter
# standard library modules
import sys, errno, re, json, ssl
from urllib import request
from urllib.error import HTTPError
from time import sleep
import itertools

In [65]:
fastaseq = 'CAZy_'+family+'_formatted_'+"{0:.0%}".format(clustercutoff)+'inclchar.fasta'

In [66]:
#Here we generate a file only containing UNIQUE sequences that can be used for InterPro domain detection
def prep_input(inputfile, interprolist, charblastdict, outputblastdict):
    """This function parses trough a given FASTA file and creates a dict of ID: sequence"""
    proteins = {}
    
    with open(fastaseq, 'r') as f:
        sequences = SeqIO.parse(f, "fasta")
        modified_sequences = []
        for seq_record in sequences:
            modified_sequences.append(seq_record)

        for identifier in interprolist:
            for seq_record in modified_sequences:
                seq_id = seq_record.id[:seq_record.id.find('_')]

                if identifier in charblastdict:
                    proteins[identifier] = outputblastdict[charblastdict[identifier]]

                elif seq_id == identifier:
                    proteins[identifier] = str(seq_record.seq)

    return proteins

def domain_detection(proteins):
    """This function uses the InterPro API and returns which domains can be found in several databases"""
    
    md5_to_id = {}
    
    domainoutput = {}
    positionoutput = {}
    databaseoutput = {}
    
    #converts the protein sequences to a hexadecimal representation in uppercase
    for identifier, sequence in proteins.items():
        md5 = hashlib.md5(sequence.encode()).hexdigest().upper()
        md5_to_id[md5] = identifier
    
        
    #print(md5_to_id)
    params = {"md5": list(md5_to_id.keys())}
    #print(params)
    data = urlencode(params, doseq=True).encode("ascii")
    #print(data)
    
    with urlopen(URL, data) as res:
        data = res.read().decode("utf-8")
    
    domain_ids = []
    unknown_ids = []
    

    root = ET.fromstring(data)
    for m in root.findall(".//match"):
        md5 = m.find("proteinMD5").text
        protein_id = md5_to_id.pop(md5) #are these the ID's of proteins that have a UniParc Identifier?
        domain_ids.append(protein_id)
        
        #print(protein_id)
        domaindictionary = {}
        positionlist = []
        databaselist = []
        
        #find domains on InterPro
        for hit in m.findall("hit"):

            #print(hit)
            columns = hit.text.split(",")
            
            fragments = []
            for frag in columns[6].split(";"):
                start, end, _ = frag.split("-")
                fragments.append((int(start), int(end)))
            
                
                domaindatabase = columns[0]
                domainname = columns[2]
                domainstart = fragments[0][0]
                domainend = fragments[0][1]
            
            domaindictionary[str([domainstart, domainend])] = domainname
            positionlist.append([domainstart, domainend])
            databaselist.append([domaindatabase, domainname])
            
            #print("\t".join([
                #protein_id,
                #columns[0],
                #columns[2],
                #",".join([f"{s}-{e}" for s, e in sorted(fragments)])
                #]))
        domainoutput[protein_id] = domaindictionary
        positionoutput[protein_id] = positionlist
        databaseoutput[protein_id] = databaselist

    
    for protein_id in md5_to_id.values():
        unknown_ids.append(protein_id)
        
        sys.stderr.write(f"No domains found in {protein_id}:"f" try to run InterProScan\n")
        
    print(domainoutput)
    print('\n')
    print(positionoutput)
    print('\n')
    print(databaseoutput)
    
    return domainoutput, positionoutput, databaseoutput


prepareinput = prep_input(fastaseq, interprolist, blastchar[0], blastchar[1])
finddomains = domain_detection(prepareinput)

{'AFY45032.1': {'[369, 787]': 'SSF48208', '[41, 372]': 'PF12215', '[421, 796]': 'PF04685', '[31, 801]': 'PTHR12654', '[1, 802]': 'PIRSF028944'}, 'QLE41800.1': {'[387, 805]': 'SSF48208', '[438, 814]': 'PF04685', '[1, 819]': 'PIRSF028944', '[31, 817]': 'PTHR12654', '[41, 389]': 'PF12215'}, 'BAZ68399.1': {'[1, 808]': 'PIRSF028944', '[423, 801]': 'PF04685', '[369, 791]': 'SSF48208', '[41, 374]': 'PF12215', '[32, 802]': 'PTHR12654'}, 'QLE57510.1': {'[1, 803]': 'PIRSF028944', '[421, 797]': 'PF04685', '[41, 372]': 'PF12215', '[360, 787]': 'SSF48208', '[31, 800]': 'PTHR12654'}, 'BAZ06285.1': {'[1, 803]': 'PIRSF028944', '[418, 795]': 'PF04685', '[365, 785]': 'SSF48208', '[42, 369]': 'PF12215', '[25, 797]': 'PTHR12654'}, 'NP': {'[151, 455]': 'PF12215', '[43, 59]': 'mobidb-lite', '[563, 876]': 'G3DSA:1.50.10.10:FF:000013', '[32, 62]': 'mobidb-lite', '[79, 896]': 'PIRSF028944', '[453, 890]': 'SSF48208', '[521, 886]': 'PF04685', '[71, 898]': 'PTHR12654'}, 'AGY57706.1': {'[1, 27]': 'SIGNAL_PEPTIDE',

In [67]:
print(finddomains[2])

{'AFY45032.1': [['SUPERFAMILY', 'SSF48208'], ['PFAM', 'PF12215'], ['PFAM', 'PF04685'], ['PANTHER', 'PTHR12654'], ['PIRSF', 'PIRSF028944']], 'QLE41800.1': [['SUPERFAMILY', 'SSF48208'], ['PFAM', 'PF04685'], ['PIRSF', 'PIRSF028944'], ['PANTHER', 'PTHR12654'], ['PFAM', 'PF12215']], 'BAZ68399.1': [['PIRSF', 'PIRSF028944'], ['PFAM', 'PF04685'], ['SUPERFAMILY', 'SSF48208'], ['PFAM', 'PF12215'], ['PANTHER', 'PTHR12654']], 'QLE57510.1': [['PIRSF', 'PIRSF028944'], ['PFAM', 'PF04685'], ['PFAM', 'PF12215'], ['SUPERFAMILY', 'SSF48208'], ['PANTHER', 'PTHR12654']], 'BAZ06285.1': [['PIRSF', 'PIRSF028944'], ['PFAM', 'PF04685'], ['SUPERFAMILY', 'SSF48208'], ['PFAM', 'PF12215'], ['PANTHER', 'PTHR12654']], 'NP': [['PFAM', 'PF12215'], ['MOBIDB_LITE', 'mobidb-lite'], ['GENE3D', 'G3DSA:1.50.10.10'], ['MOBIDB_LITE', 'mobidb-lite'], ['FUNFAM', 'G3DSA:1.50.10.10:FF:000013'], ['PIRSF', 'PIRSF028944'], ['SUPERFAMILY', 'SSF48208'], ['PFAM', 'PF04685'], ['PANTHER', 'PTHR12654']], 'AGY57706.1': [['PHOBIUS', 'SIGNAL_

In [72]:
def get_domain_name(databaseoutput):
    """This function retrieves the appropriate name for each found domain. it converts the InterPro ID to the corresponding name"""
    
    ROOTURL = 'https://www.ebi.ac.uk/interpro/api/entry/'
    entryDB = {'GENE3D':'cathgene3d', 'CDD':'cdd', 'HAMAP':'hamap', 'PANTHER':'panther', 'PFAM':'pfam', 'PIRSF':'pirsf', 'PRINTS':'prints', 'PROSITE_PROFILES':'profile', 'PROSITE_PATTERNS':'prosite', 'SFLD':'sfld', 'SMART':'smart', 'SUPERFAMILY':'ssf', 'TIGRFAMS':'tigrfams'}
    
    domainnamelist = {}
    domainnamedictionary = {}
    

    for key, value in databaseoutput.items():
        templist = []
        tempdict = {}
        
        for domain in value:

            if domain[0] in entryDB:
                
                #disable SSL verification to avoid config issues
                context = ssl._create_unverified_context()
                
                next = ROOTURL + entryDB[domain[0]] + '/' + domain[1]
                last_page = False
                attempts = 0
                
                while next:
                    try:
                        
                        req = request.Request(next, headers={"Accept": "application/json"})
                        res = request.urlopen(req, context=context)
                        # If the API times out due a long running query
                        if res.status == 408:
                        # wait just over a minute
                            sleep(61)
                        # then continue this loop with the same URL
                            continue
                            
                        elif res.status == 204:
                            print('sorry no data could be retrieved for this entry' + '\n')
                            break
                            
                        elif res.status == 404:
                            print('sorry no data could be retrieved for this entry' + '\n')
                            break

                        payload = json.loads(res.read().decode())
                        attempts = 0
                        #next = payload["next"]
                        #if not next:
                            #last_page = True
                            
                        last_page = True
                        next = False #needed to avoid loop

                    except HTTPError as e:
                        if e.code == 408:
                            sleep(61)
                            continue
                        else:
                            #If there is a different HTTP error, it wil re-try 3 times before failing
                            if attempts < 3:
                                attempts += 1
                                sleep(61)
                                continue
                            else:
                                sys.stderr.write("LAST URL: " + next)
                                raise e

                    name = str(payload['metadata']['name']['name'])
                    
                    #if name != 'None':
                        #print(name)
                    tempdict[name] = domain[0]  
                    templist.append([domain[0], name])

                    if next:
                        sleep(1)
                sleep(1)
            else:
                tempdict[domain[1]] = domain[0]
                templist.append(domain)
        
        #print(templist)        
        domainnamedictionary[key] = tempdict
        domainnamelist[key] = templist
        
    #print(domainnamedictionary) 
    print('\n')
    print(domainnamelist)
    return domainnamelist, domainnamedictionary
finddomainnames = get_domain_name(finddomains[2])

AFY45032.1
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF12215']
['PFAM', 'PF04685']
['PANTHER', 'PTHR12654']
['PIRSF', 'PIRSF028944']
QLE41800.1
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF04685']
['PIRSF', 'PIRSF028944']
['PANTHER', 'PTHR12654']
['PFAM', 'PF12215']
BAZ68399.1
['PIRSF', 'PIRSF028944']
['PFAM', 'PF04685']
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF12215']
['PANTHER', 'PTHR12654']
QLE57510.1
['PIRSF', 'PIRSF028944']
['PFAM', 'PF04685']
['PFAM', 'PF12215']
['SUPERFAMILY', 'SSF48208']
['PANTHER', 'PTHR12654']
BAZ06285.1
['PIRSF', 'PIRSF028944']
['PFAM', 'PF04685']
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF12215']
['PANTHER', 'PTHR12654']
NP
['PFAM', 'PF12215']
['MOBIDB_LITE', 'mobidb-lite']
['GENE3D', 'G3DSA:1.50.10.10']
['MOBIDB_LITE', 'mobidb-lite']
['FUNFAM', 'G3DSA:1.50.10.10:FF:000013']
['PIRSF', 'PIRSF028944']
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF04685']
['PANTHER', 'PTHR12654']
AGY57706.1
['PHOBIUS', 'SIGNAL_PEPTIDE']
['PHOBIUS', 'SIGNAL_PEPTIDE_C_REGION']
['PHOBIUS', 'NON_CYT

['PIRSF', 'PIRSF028944']
['PANTHER', 'PTHR12654']
CAH0702348.1
['MOBIDB_LITE', 'mobidb-lite']
['GENE3D', 'G3DSA:1.50.10.10']
['MOBIDB_LITE', 'mobidb-lite']
['PANTHER', 'PTHR12654']
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF12215']
['PIRSF', 'PIRSF028944']
['COILS', 'Coil']
['MOBIDB_LITE', 'mobidb-lite']
['PFAM', 'PF04685']
['MOBIDB_LITE', 'mobidb-lite']
['PIRSF', 'PIRSF028944']
CAH0714467.1
['SUPERFAMILY', 'SSF48208']
['PANTHER', 'PTHR12654']
['GENE3D', 'G3DSA:1.50.10.10']
['PIRSF', 'PIRSF028944']
['PFAM', 'PF12215']
['PIRSF', 'PIRSF028944']
['PFAM', 'PF04685']
['MOBIDB_LITE', 'mobidb-lite']
['MOBIDB_LITE', 'mobidb-lite']
CAH2991170.1
['PIRSF', 'PIRSF028944']
['PIRSF', 'PIRSF028944']
['MOBIDB_LITE', 'mobidb-lite']
['MOBIDB_LITE', 'mobidb-lite']
['PFAM', 'PF04685']
['PANTHER', 'PTHR12654']
['PFAM', 'PF12215']
['SUPERFAMILY', 'SSF48208']
['MOBIDB_LITE', 'mobidb-lite']
['GENE3D', 'G3DSA:1.50.10.10']
CAG9785611.1
['MOBIDB_LITE', 'mobidb-lite']
['GENE3D', 'G3DSA:1.50.10.10']
['PANTHER', 'PTHR

['MOBIDB_LITE', 'mobidb-lite']
ADY41918.1
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF04685']
['PFAM', 'PF12215']
['SUPERFAMILY', 'SSF48208']
['PANTHER', 'PTHR12654']
ASC70763.1
['PANTHER', 'PTHR12654']
['PFAM', 'PF12215']
AER98954.1
['MOBIDB_LITE', 'mobidb-lite']
['MOBIDB_LITE', 'mobidb-lite']
EAL61202.1
['MOBIDB_LITE', 'mobidb-lite']
['PFAM', 'PF12215']
['MOBIDB_LITE', 'mobidb-lite']
['PFAM', 'PF04685']
['MOBIDB_LITE', 'mobidb-lite']
['SUPERFAMILY', 'SSF48208']
['GENE3D', 'G3DSA:1.50.10.10']
['PANTHER', 'PTHR12654']
['FUNFAM', 'G3DSA:1.50.10.10:FF:000083']
['MOBIDB_LITE', 'mobidb-lite']
['MOBIDB_LITE', 'mobidb-lite']
EDQ75122.1
['MOBIDB_LITE', 'mobidb-lite']
['PANTHER', 'PTHR12654']
['PFAM', 'PF12215']
['SUPERFAMILY', 'SSF48208']
['FUNFAM', 'G3DSA:1.50.10.10:FF:000006']
['PIRSF', 'PIRSF028944']
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF04685']
['MOBIDB_LITE', 'mobidb-lite']
EDQ64036.1
['PIRSF', 'PIRSF028944']
['TMHMM', 'TMhelix']
['PFAM', 'PF04685']
['MOBIDB_LITE', 'mobidb-lite']
['G

['PHOBIUS', 'SIGNAL_PEPTIDE_N_REGION']
['PHOBIUS', 'NON_CYTOPLASMIC_DOMAIN']
['PHOBIUS', 'SIGNAL_PEPTIDE']
['PROSITE_PATTERNS', 'PS00018']
['PIRSF', 'PIRSF028944']
['PFAM', 'PF04685']
['SUPERFAMILY', 'SSF48208']
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF12215']
['PANTHER', 'PTHR12654']
['PHOBIUS', 'SIGNAL_PEPTIDE_C_REGION']
CAO46877.1
['PFAM', 'PF12215']
['GENE3D', 'G3DSA:1.50.10.10']
['PANTHER', 'PTHR12654']
['MOBIDB_LITE', 'mobidb-lite']
['PFAM', 'PF04685']
['PIRSF', 'PIRSF028944']
['FUNFAM', 'G3DSA:1.50.10.10:FF:000006']
['MOBIDB_LITE', 'mobidb-lite']
['SUPERFAMILY', 'SSF48208']
QHO62870.1
['PFAM', 'PF04685']
['PANTHER', 'PTHR12654']
BAA97011.1
['PIRSF', 'PIRSF028944']
['PFAM', 'PF12215']
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF12215']
['PIRSF', 'PIRSF028944']
['PFAM', 'PF04685']
['SUPERFAMILY', 'SSF48208']
['COILS', 'Coil']
['FUNFAM', 'G3DSA:1.50.10.10:FF:000006']
['MOBIDB_LITE', 'mobidb-lite']
['PANTHER', 'PTHR12654']
BAE99037.1
['PFAM', 'PF12215']
['FUNFAM', 'G3DSA:1.50.10.10

['PHOBIUS', 'SIGNAL_PEPTIDE_N_REGION']
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF12215']
['PHOBIUS', 'SIGNAL_PEPTIDE_C_REGION']
QTH40464.1
['SUPERFAMILY', 'SSF48208']
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF04685']
['PFAM', 'PF12215']
['PANTHER', 'PTHR12654']
QNK59397.1
['PANTHER', 'PTHR12654']
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF12215']
['PFAM', 'PF04685']
['SUPERFAMILY', 'SSF48208']
QTH43032.1
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF12215']
['PFAM', 'PF04685']
['SUPERFAMILY', 'SSF48208']
['PANTHER', 'PTHR12654']
UVI29285.1
['PFAM', 'PF04685']
['SUPERFAMILY', 'SSF48208']
['GENE3D', 'G3DSA:1.50.10.10']
['PANTHER', 'PTHR12654']
['PFAM', 'PF12215']
AZN39191.1
['GENE3D', 'G3DSA:1.50.10.10']
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF04685']
['PFAM', 'PF12215']
['PANTHER', 'PTHR12654']
QHW30569.1
['GENE3D', 'G3DSA:1.50.10.10']
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF04685']
['PANTHER', 'PTHR12654']
['PFAM', 'PF12215']
QJD86308.1
['GENE3D', 'G3DSA:2.60.120.1390']
['GENE3D', 'G3DS

...

['PHOBIUS', 'NON_CYTOPLASMIC_DOMAIN']
['PANTHER', 'PTHR12654']
['GENE3D', 'G3DSA:1.50.10.10']
['PHOBIUS', 'SIGNAL_PEPTIDE_N_REGION']
['TMHMM', 'TMhelix']
['PHOBIUS', 'SIGNAL_PEPTIDE']
['PFAM', 'PF04685']
CAZ94527.1
['PHOBIUS', 'NON_CYTOPLASMIC_DOMAIN']
['PFAM', 'PF12215']
['MOBIDB_LITE', 'mobidb-lite']
['GENE3D', 'G3DSA:1.50.10.10']
['PANTHER', 'PTHR12654']
['PHOBIUS', 'SIGNAL_PEPTIDE_C_REGION']
['PHOBIUS', 'SIGNAL_PEPTIDE_N_REGION']
['PHOBIUS', 'SIGNAL_PEPTIDE']
['PHOBIUS', 'SIGNAL_PEPTIDE_H_REGION']
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF04685']
AQQ71108.1
['PFAM', 'PF04685']
['SUPERFAMILY', 'SSF48208']
['GENE3D', 'G3DSA:1.50.10.10']
['PANTHER', 'PTHR12654']
UOY04881.1
['PHOBIUS', 'SIGNAL_PEPTIDE_H_REGION']
['PHOBIUS', 'SIGNAL_PEPTIDE_N_REGION']
['SIGNALP_EUK', 'SignalP-noTM']
['PANTHER', 'PTHR12654']
['PHOBIUS', 'SIGNAL_PEPTIDE']
['SIGNALP_GRAM_NEGATIVE', 'SignalP-noTM']
['PFAM', 'PF12215']
['SUPERFAMILY', 'SSF48208']
['PHOBIUS', 'SIGNAL_PEPTIDE_C_REGION']
['PHOBIUS', 'NON_CYTOPLAS

AOL16816.1
['PFAM', 'PF04685']
['SUPERFAMILY', 'SSF48208']
['GENE3D', 'G3DSA:1.50.10.10']
['PANTHER', 'PTHR12654']
AWR96887.1
['GENE3D', 'G3DSA:1.50.10.10']
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF04685']
['PFAM', 'PF12215']
['PANTHER', 'PTHR12654']
AEE93223.1
['SUPERFAMILY', 'SSF48208']
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF04685']
['PANTHER', 'PTHR12654']
['PFAM', 'PF12215']
QGR19609.1
['GENE3D', 'G3DSA:1.50.10.10']
['PHOBIUS', 'NON_CYTOPLASMIC_DOMAIN']
['PANTHER', 'PTHR12654']
['PHOBIUS', 'CYTOPLASMIC_DOMAIN']
['PFAM', 'PF12215']
['PFAM', 'PF04685']
['PHOBIUS', 'TRANSMEMBRANE']
['SUPERFAMILY', 'SSF48208']
BCU70026.1
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF04685']
['PANTHER', 'PTHR12654']
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF12215']
ARM75470.1
['GENE3D', 'G3DSA:1.50.10.10']
['PANTHER', 'PTHR12654']
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF04685']
['PFAM', 'PF12215']
AWR93938.1
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF12215']
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF04685']

['SMART', 'SM00606']
['MOBIDB_LITE', 'mobidb-lite']
['PHOBIUS', 'SIGNAL_PEPTIDE_N_REGION']
['PHOBIUS', 'NON_CYTOPLASMIC_DOMAIN']
['PFAM', 'PF12215']
['SUPERFAMILY', 'SSF48208']
['SIGNALP_GRAM_POSITIVE', 'SignalP-TM']
['PHOBIUS', 'SIGNAL_PEPTIDE_C_REGION']
['PROSITE_PROFILES', 'PS51175']
['GENE3D', 'G3DSA:2.60.120.260']
['SIGNALP_EUK', 'SignalP-noTM']
['PFAM', 'PF03422']
['PANTHER', 'PTHR12654']
['PHOBIUS', 'SIGNAL_PEPTIDE']
['TMHMM', 'TMhelix']
['SUPERFAMILY', 'SSF49785']
['PHOBIUS', 'SIGNAL_PEPTIDE_H_REGION']
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF04685']
CAH1394245.1
['PFAM', 'PF04685']
['PANTHER', 'PTHR12654']
UQZ36148.1
['SUPERFAMILY', 'SSF49785']
['PFAM', 'PF03512']
['PFAM', 'PF04685']
['GENE3D', 'G3DSA:2.60.120.260']
['PFAM', 'PF03422']
['SMART', 'SM00606']
['GENE3D', 'G3DSA:2.60.120.260']
['GENE3D', 'G3DSA:1.50.10.10']
['CDD', 'cd04084']
['PANTHER', 'PTHR12654']
['PROSITE_PROFILES', 'PS51175']
['SUPERFAMILY', 'SSF48208']
['SUPERFAMILY', 'SSF49785']
['PFAM', 'PF00754']
AUO202

['PANTHER', 'PTHR12654']
['PFAM', 'PF04685']
['PIRSF', 'PIRSF028944']
['PFAM', 'PF12215']
AOY83708.1
['PFAM', 'PF12215']
['GENE3D', 'G3DSA:1.50.10.10']
['SUPERFAMILY', 'SSF48208']
['PANTHER', 'PTHR12654']
['PFAM', 'PF04685']
['PIRSF', 'PIRSF028944']
AFY39644.1
['PFAM', 'PF12215']
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF04685']
['GENE3D', 'G3DSA:1.50.10.10']
['PIRSF', 'PIRSF028944']
['PANTHER', 'PTHR12654']
BAW97599.1
['PANTHER', 'PTHR12654']
['SUPERFAMILY', 'SSF48208']
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF12215']
['PFAM', 'PF04685']
['PIRSF', 'PIRSF028944']
ADN13525.1
['SUPERFAMILY', 'SSF48208']
['PIRSF', 'PIRSF028944']
['PANTHER', 'PTHR12654']
['PFAM', 'PF04685']
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF12215']
AFZ16565.1
['PIRSF', 'PIRSF028944']
['PFAM', 'PF12215']
['PANTHER', 'PTHR12654']
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF04685']
['SUPERFAMILY', 'SSF48208']
CAD5915932.1
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF12215']
['PFAM', 'PF04685']
['PIRSF', 'PIRSF028944']
[

['PFAM', 'PF12215']
['SUPERFAMILY', 'SSF48208']
['PANTHER', 'PTHR12654']
['MOBIDB_LITE', 'mobidb-lite']
['GENE3D', 'G3DSA:1.50.10.10']
['PFAM', 'PF04685']
['MOBIDB_LITE', 'mobidb-lite']
QNI68074.1
['PANTHER', 'PTHR12654']
['GENE3D', 'G3DSA:1.50.10.10']
['SUPERFAMILY', 'SSF48208']
['PFAM', 'PF12215']
['PIRSF', 'PIRSF028944']
['PFAM', 'PF04685']
QNI94073.1
['PFAM', 'PF04685']
['SUPERFAMILY', 'SSF48208']
['PANTHER', 'PTHR12654']
['PIRSF', 'PIRSF028944']
['PFAM', 'PF12215']
['GENE3D', 'G3DSA:1.50.10.10']
AKN60016.1
['PFAM', 'PF12215']
['PIRSF', 'PIRSF028944']
['PFAM', 'PF04685']
['SUPERFAMILY', 'SSF48208']
['GENE3D', 'G3DSA:1.50.10.10']
['PANTHER', 'PTHR12654']
AII43980.1
['PFAM', 'PF12215']
['PFAM', 'PF04685']
['PIRSF', 'PIRSF028944']
['GENE3D', 'G3DSA:1.50.10.10']
['SUPERFAMILY', 'SSF48208']
['PANTHER', 'PTHR12654']
BAY86896.1
['PHOBIUS', 'CYTOPLASMIC_DOMAIN']
['PANTHER', 'PTHR12654']
['PIRSF', 'PIRSF028944']
['PHOBIUS', 'NON_CYTOPLASMIC_DOMAIN']
['PFAM', 'PF04685']
['PHOBIUS', 'TRANSMEM

In [73]:

def position_domains_dict(positiondict, domaindict):
    """Creates a dictionary that contains for every entry, for every found domainpositions, the corresponding domainname"""
    
    alldomainsdict = {}
    for key, value in positiondict.items():
        tempdict = {}
        print(key)
        for positions in value:
            placeinlist = value.index(positions)
            domainsinseq = domaindict[key]
            domainlist = domainsinseq[placeinlist]
            print(domainlist)
            tempdict[str(positions)] = domainlist[1] 
        alldomainsdict[key] = tempdict
            
            
            
    print(alldomainsdict)
    
    return alldomainsdict

all_domains_in_seq = position_domains_dict(finddomains[1], finddomainnames[0])

AFY45032.1
['SUPERFAMILY', 'Six-hairpin glycosidases']
['PFAM', 'beta-glucosidase 2, glycosyl-hydrolase family 116 N-term']
['PFAM', 'Glycosyl-hydrolase family 116, catalytic region']
['PANTHER', 'BILE ACID BETA-GLUCOSIDASE-RELATED']
['PIRSF', 'Beta-glucosidase, GBA2 type']
QLE41800.1
['SUPERFAMILY', 'Six-hairpin glycosidases']
['PFAM', 'Glycosyl-hydrolase family 116, catalytic region']
['PIRSF', 'Beta-glucosidase, GBA2 type']
['PANTHER', 'BILE ACID BETA-GLUCOSIDASE-RELATED']
['PFAM', 'beta-glucosidase 2, glycosyl-hydrolase family 116 N-term']
BAZ68399.1
['PIRSF', 'Beta-glucosidase, GBA2 type']
['PFAM', 'Glycosyl-hydrolase family 116, catalytic region']
['SUPERFAMILY', 'Six-hairpin glycosidases']
['PFAM', 'beta-glucosidase 2, glycosyl-hydrolase family 116 N-term']
['PANTHER', 'BILE ACID BETA-GLUCOSIDASE-RELATED']
QLE57510.1
['PIRSF', 'Beta-glucosidase, GBA2 type']
['PFAM', 'Glycosyl-hydrolase family 116, catalytic region']
['PFAM', 'beta-glucosidase 2, glycosyl-hydrolase family 116 N-t

['PANTHER', 'BILE ACID BETA-GLUCOSIDASE-RELATED']
['PFAM', 'beta-glucosidase 2, glycosyl-hydrolase family 116 N-term']
['PHOBIUS', 'SIGNAL_PEPTIDE_N_REGION']
['SUPERFAMILY', 'Six-hairpin glycosidases']
['PHOBIUS', 'SIGNAL_PEPTIDE_C_REGION']
AQT69739.1
['GENE3D', 'None']
['PFAM', 'Glycosyl-hydrolase family 116, catalytic region']
['PHOBIUS', 'NON_CYTOPLASMIC_DOMAIN']
['SUPERFAMILY', 'Six-hairpin glycosidases']
['PFAM', 'beta-glucosidase 2, glycosyl-hydrolase family 116 N-term']
['PANTHER', 'BILE ACID BETA-GLUCOSIDASE-RELATED']
['PHOBIUS', 'SIGNAL_PEPTIDE_N_REGION']
['PFAM', 'TAT (twin-arginine translocation) pathway signal sequence']
['PHOBIUS', 'SIGNAL_PEPTIDE_C_REGION']
['PHOBIUS', 'SIGNAL_PEPTIDE_H_REGION']
['PFAM', 'beta-glucosidase 2, glycosyl-hydrolase family 116 N-term']
['PROSITE_PROFILES', 'Twin arginine translocation (Tat) signal profile']
['PROSITE_PROFILES', 'Twin arginine translocation (Tat) signal profile']
QWF83655.1
['PFAM', 'beta-glucosidase 2, glycosyl-hydrolase family

In [74]:
def overlap(a, b):
    
    x1, y1 = a[0], a[1]
    length1 = y1 - x1
    
    x2, y2 = b[0], b[1]
    length2 = y2 - x2
    
    if y1 in range(x2, y2+1):
        #in the uncommon scenario that a 'domain' only consists of 1 AA
        if x1 == y1 or x2 == y2:
            identity = 1
        else:
            over = y1 - x2
            identity = min(over/length1,over/length2)
        
    elif x2 in range (x1, y1+1) and y2 in range(x1, y1+1):
        identity = length2/length1
    
    else:
        identity = 0
    
    return(identity > 0.50)
        
def extract_overlap(domainlist):
    outputlist = []
    templist = []
    
    domainlist = sorted(domainlist, key=lambda x: (x[0], x[1]))
    
    i = 0
    while i in range(len(domainlist)):
        
        if i == len(domainlist) - 1:
            if len(templist) != 0:
                #remove doubles from templist
                templist.sort()
                templist = list(templist for templist,_ in itertools.groupby(templist))
                outputlist.append(templist)
            else:
                outputlist.append(domainlist[i])
            break
            
        elif overlap(domainlist[i], domainlist[i+1]) == True:
            templist += domainlist[i], domainlist[i+1]
            i += 1
            
        else:
            
            if len(templist) != 0:
                #remove doubles from templist
                templist.sort()
                templist = list(templist for templist,_ in itertools.groupby(templist))
                outputlist.append(templist)
                templist = [] 
                
            else:
                outputlist.append(domainlist[i])
            i += 1
    return outputlist

extract_overlap_dict = {}

for key, value in finddomains[1].items():


    test = extract_overlap(value)
    extract_overlap_dict[key] = test
print(extract_overlap_dict)


{'AFY45032.1': [[[1, 802], [31, 801]], [41, 372], [[369, 787], [421, 796]]], 'QLE41800.1': [[[1, 819], [31, 817]], [41, 389], [[387, 805], [438, 814]]], 'BAZ68399.1': [[[1, 808], [32, 802]], [41, 374], [[369, 791], [423, 801]]], 'QLE57510.1': [[[1, 803], [31, 800]], [41, 372], [[360, 787], [421, 797]]], 'BAZ06285.1': [[[1, 803], [25, 797]], [42, 369], [[365, 785], [418, 795]]], 'NP': [[[32, 62], [43, 59]], [[71, 898], [79, 896]], [151, 455], [[453, 890], [521, 886], [563, 876]]], 'AGY57706.1': [[1, 8], [[1, 24], [1, 25], [1, 27], [1, 37]], [9, 19], [20, 27], [[20, 845], [28, 854], [66, 843]], [75, 412], [412, 441], [[474, 836], [529, 800]]], 'CAN94573.1': [[1, 20], [1, 79], [32, 52], [[70, 781], [96, 778]], [97, 371], [[384, 772], [427, 773], [463, 780]]], 'ACO61507.1': [[1, 6], [[1, 18], [1, 20]], [7, 15], [16, 20], [[21, 954], [58, 937]], [63, 419], [125, 145], [437, 456], [500, 519], [[537, 927], [557, 926]], [603, 623], [672, 929]], 'EEH53657.1': [[1, 5], [[1, 26], [1, 31], [1, 32]

In [75]:
def clean_domains(domainlist, alldomainsdict, databaseoutput):
    #print(f'{domainlist} \n {alldomainsdict} \n {databaseoutput}')
    
    databasepreference = ['SMART', 'PFAM', 'PROFILE', 'GENE3D', 'SUPERFAMILY' ]
    finaldomainoutput = {}
    for key, value in domainlist.items():
        temporaryoutput = []
        for domain in value:
            #temporaryoutput = []

            if all(isinstance(x, int) for x in domain):
                dname = alldomainsdict[key][str(domain)]
                db = databaseoutput[key][dname]
                
                #we'll not include signal peptides
                #also for some domains we could not retrieve a name. These domains are called 'None' and will not be included
                if dname != 'None' and db != 'PHOBIUS' and db.upper().find('SIGNAL') == -1: #and db != 'COILS'
                    #temporaryoutput[key] = domain
                    temporaryoutput.append([domain, dname])
                    
            else:
                #this means that we have multiple positions describing the same domain
                tempdict = {}
                tempposition = {}
                for simdomain in domain:
                    dname = alldomainsdict[key][str(simdomain)]
                    print(dname)
                    db = databaseoutput[key][dname]
                    
                    #we'll not include signal peptides
                    if dname != 'None' and db != 'PHOBIUS' and db.upper().find('SIGNAL') == -1: #db != 'COILS'
                        tempdict[dname] = db
                        tempposition[dname] = simdomain
                
                if bool(tempdict) == True:
                    #print(key)
                    #print(tempdict)
                    count = 1
                    stop = 0
                    
                    for k, v in tempdict.items():
                        while stop == 0:
                        
                            if count == len(tempdict):
                                dom = list(tempposition.keys())[0]
                                #temporaryoutput[str(tempposition[dom])] = dom
                                temporaryoutput.append([tempposition[dom], dom])
                                stop = 1


                            else:
                                for i in range(len(databasepreference)): #+1

                                    #if i == len(databasepreference):
                                        #dom = list(tempposition.keys())[0]
                                        #temporaryoutput[str(tempposition[dom])] = dom

                                    if v == databasepreference[i]:
                                        #temporaryoutput[str(tempposition[k])] = k
                                        temporaryoutput.append([tempposition[k], k])
                                        stop = 1

                                    else:
                                        i+= 1

                                count += 1
                            
                
        finaldomainoutput[key] = temporaryoutput      
    print(finaldomainoutput)    
    return finaldomainoutput

finaldomainarchitecture = clean_domains(extract_overlap_dict, all_domains_in_seq, finddomainnames[1] )

Beta-glucosidase, GBA2 type
BILE ACID BETA-GLUCOSIDASE-RELATED
Six-hairpin glycosidases
Glycosyl-hydrolase family 116, catalytic region
Beta-glucosidase, GBA2 type
BILE ACID BETA-GLUCOSIDASE-RELATED
Six-hairpin glycosidases
Glycosyl-hydrolase family 116, catalytic region
Beta-glucosidase, GBA2 type
BILE ACID BETA-GLUCOSIDASE-RELATED
Six-hairpin glycosidases
Glycosyl-hydrolase family 116, catalytic region
Beta-glucosidase, GBA2 type
BILE ACID BETA-GLUCOSIDASE-RELATED
Six-hairpin glycosidases
Glycosyl-hydrolase family 116, catalytic region
Beta-glucosidase, GBA2 type
BILE ACID BETA-GLUCOSIDASE-RELATED
Six-hairpin glycosidases
Glycosyl-hydrolase family 116, catalytic region
mobidb-lite
mobidb-lite
BILE ACID BETA-GLUCOSIDASE-RELATED
Beta-glucosidase, GBA2 type
Six-hairpin glycosidases
Glycosyl-hydrolase family 116, catalytic region
None
SignalP-noTM
SignalP-TM
SIGNAL_PEPTIDE
Twin arginine translocation (Tat) signal profile
Beta-glucosidase, GBA2 type
NON_CYTOPLASMIC_DOMAIN
BILE ACID BETA-G

# Domain visualisation

In [ ]:
#QQV06122.1': [[[20, 37], 'TMhelix'], [[73, 362], '(Trans)glycosidases'], [[587, 670], 'Bacterial Ig-like domain 2'], [[829, 910], 'Bacterial Ig-like domain 2'], [[1058, 1140], 'None'], [[1132, 1277], 'Coagulation factors 5/8 type C domain (FA58C) profile'], [[1282, 1358], 'Bacterial Ig-like domain 2'], [[1441, 1461], 'Coil'], [[1511, 1531], 'Coil'], [[1513, 1586], 'AF1782-like'], [[1541, 1561], 'Coil'], [[1605, 1646], 'Coil'], [[1648, 1735], 'AF1782-like'], [[1672, 1692], 'Coil'], [[1710, 1734], 'mobidb-lite'], [[1740, 1759], 'TMhelix']]

In [ ]:
#TO DO: Find out why some domain names are 'None'

In [79]:
phyltree = 'CAZy_'+family+'phyltree.nwk'
proteinseq = 'CAZy_'+family+'_formatted_'+"{0:.0%}".format(clustercutoff)+'inclchar.fasta'

In [105]:
from ete3 import Tree, SeqMotifFace, TreeStyle, add_face_to_node


def parse_prot_seq(fastafile):
    
    with open(fastafile, 'r') as f:
        sequences = SeqIO.parse(f, "fasta")
        modified_sequences = []
        
        for seq_record in sequences:
            modified_sequences.append(seq_record)
    
    return modified_sequences
    
def get_motifs(protein, shapedict, colordict):
    
    numberofshapes = len(shapedict)
    numberofcolors = len(colordict)
    
    shapes = ['[]', 'o', '()', '^', '<>', 'o', 'v']
    colors =  ['red', 'green', 'blue', 'yellow', 'purple', 'orange', 'pink', 'cyan', 'magenta', 'gray', 'black', 'white']
    
    proteinmotif = []
    
    for key, value in protein.items():
        for domains in value:
            domainname = domains[1]
            domainstart = domains[0][0]
            domainend = domains[0][1]
            
            if domainname not in shapedict:
                shapedict[domainname] = shapes[numberofshapes%len(shapes)]
                
            if domainname not in colordict:
                colordict[domainname] = colors[numberofcolors%len(colors)]
            
            # [seq.start, seq.end, shape, width, height, fgcolor, bgcolor]
            domainmotif = [
                domainstart, domainend, shapedict[domainname], None, 15, colordict[domainname], colordict[domainname],f'arial|20|white|{domainname}']
           
            proteinmotif.append(domainmotif)


    return proteinmotif

def domain_vis(tree, finaldomainoutput, proteinsequences):
    
    protseq = parse_prot_seq(proteinsequences)
    
    #inputtree
    t = Tree(tree)
    
    shapedict = {}
    colordict = {}
    
    for key, value in finaldomainoutput.items():
        
        domotif = get_motifs({key:value}, shapedict, colordict)
        print(key)
        #print(value)
        
        for seq_record in protseq:
            
            if seq_record.id.find('_') >2: 
                proteinidentifier = seq_record.id.split('_')[0]
                
            else:
                proteinidentifier = seq_record.id.split('_')[0]+'_'+seq_record.id.split('_')[1]
                #print(proteinidentifier)


            #print(proteinidentifier)
            if proteinidentifier == key:
                print(proteinidentifier)
                seq = str(seq_record.seq)
                leaf = seq_record.id
                
                if leaf.find('(') != -1:
                    leaf = leaf.split('(')[0]
     
            
    
                seqFace = SeqMotifFace(seq, motifs=domotif, seq_format="-")
                (t & leaf).add_face(seqFace, 0, "aligned")
    

    
    
    print(shapedict)
    print(colordict)
    return t

#testdict = finaldomainarchitecture
test = domain_vis(phyltree, finaldomainarchitecture, proteinseq)

t = test
ts = TreeStyle()
ts.show_leaf_name = True

ts.tree_width = 100
ts.branch_vertical_margin = 15

#circular representation 
ts.mode = "c"
ts.arc_start = -180 # 0 degrees = 3 o'clock
ts.arc_span = 359

#add title
ts.title.add_face(TextFace(f"{family} Phylogenetic Tree", fsize=20), column=0)

t.show(tree_style=ts)


AFY45032.1
AFY45032.1
QLE41800.1
QLE41800.1
BAZ68399.1
BAZ68399.1
QLE57510.1
QLE57510.1
BAZ06285.1
BAZ06285.1
NP
AGY57706.1
AGY57706.1
CAN94573.1
CAN94573.1
ACO61507.1
ACO61507.1
EEH53657.1
EEH53657.1
ABX02953.1
ABX02953.1
AEF18218.1
AEF18218.1
AEU36563.1
AEU36563.1
ADV81312.1
ADV81312.1
QNI34795.1
QNI34795.1
ABF40689.1
ABF40689.1
AQQ71109.1
AQQ71109.1
AYY13601.1
AYY13601.1
UPK77053.1
UPK77053.1
BAB13431.1
BAB13431.1
BAD32491.1
BAD32491.1
CAM17042.1
CAM17042.1
CAI10981.1
CAI10981.1
EDL02462.1
EDL02462.1
AAI60640.1
AAI60640.1
VUY95630.1
VUY95630.1
CAG12815.1
CAG12815.1
AWO97544.1
AWO97544.1
AHH37418.1
AHH37418.1
AFO96150.1
AFO96150.1
XP
CAB3248405.1
CAB3248405.1
CAH0702348.1
CAH0702348.1
CAH0714467.1
CAH0714467.1
CAH2991170.1
CAH2991170.1
CAG9785611.1
CAG9785611.1
CAH0581399.1
CAH0581399.1
CAF3001293.1
CAF3001293.1
CAG9821274.1
CAG9821274.1
CAH1113965.1
CAH1113965.1
CAG9854271.1
CAG9854271.1
CAG9829466.1
CAG9829466.1
QQP35851.1
QQP35851.1
CAG9765704.1
CAG9765704.1
CAH0551459.1
CAH055145

In [ ]:
#To DO: when formatting the file, cut off seq_id when '()' are present in the id. FastTree doesn't handle these 